# **Transcription with Conversation-Level Sentiment Annotations**
Below, we use the Hume and GPT APIs to generate conversation-level sentiment annotations for a Zoom conversation.

> We design a two-part pipeline to visualize Zoom meetings with conversation-level sentiment annotations. We first introduce novel metrics to capture conversation-level sentiments along three axes: comprehension, consensus, and cordiality. To obtain these metrics, we first identify each speaker's individual expressed sentiments during each of their responses. To determine speaker sentiment, we segment Zoom recordings by speaker and feed the video data, audio file (including information on voice prosity), and transcript (text content) of each segment to an off-the-shelf model that outputs a quantitative measure of the extent to which the speaker expresses 48 emotions. Afterward, for each segment, we combine the speaker's top 5 emotions with weights, uniformly sampled facial expressions, and spoken words in an instruction-tuned prompt to a multimodal large language model in order to determine conversation-level metrics.



# Initialization

In [1]:
# Install libraries
!pip install hume
!pip install hume[stream]
!pip install openai
!pip install python-dotenv
!pip install pydub
!pip install ffmpeg
!pip install moviepy
!pip install webvtt-py
!pip install opencv-python


^C


In [1]:
import os
from dotenv import load_dotenv
from openai import OpenAI
import requests
import base64
from pydub import AudioSegment
from hume import HumeBatchClient
import json
import pandas as pd
import matplotlib.pyplot as plt
# from google.colab import userdata
import webvtt
# from google.colab import userdata
import cv2
from moviepy.editor import VideoFileClip
import subprocess

## Merge three Modalities

## 1. Merge language to sentenses, and average scores for each emotions

In [14]:
import os
import json

def process_json_file(filepath, output_directory):
    # Determine output file path
    output_path = os.path.join(output_directory, os.path.basename(filepath).replace('_lang.json', '_lang_processed.json'))
    
    # Skip processing if the file already exists
    if os.path.exists(output_path):
        # print(f"Skipping existing file: {output_path}")
        return
    
    # Read JSON file
    with open(filepath, 'r') as file:
        data = json.load(file)

    print("processing:" , filepath)
    # Navigate to the predictions in JSON structure
    predictions = data[0]["results"]["predictions"][0]["models"]["language"]["grouped_predictions"][0]["predictions"]

    # Calculate average emotion scores
    emotion_scores = {}
    count_emotions = {}
    for pred in predictions:
        for emotion in pred["emotions"]:
            if emotion["name"] in emotion_scores:
                emotion_scores[emotion["name"]] += emotion["score"]
                count_emotions[emotion["name"]] += 1
            else:
                emotion_scores[emotion["name"]] = emotion["score"]
                count_emotions[emotion["name"]] = 1
    
    # Averaging the scores
    average_emotion_scores = {emotion: score / count_emotions[emotion] for emotion, score in emotion_scores.items()}
    
    # Simplify the output format to just language and emotions
    lang = {"lang": average_emotion_scores}
    
    # Save processed data to a new file
    with open(output_path, 'w') as outfile:
        json.dump(lang, outfile, indent=4)
    print(f"Processed and saved: {output_path}")

# Directories
input_directory = "./dataset/outputs/hume"
output_directory = "./dataset/outputs/hume_processed"

# Create the output directory if it does not exist
os.makedirs(output_directory, exist_ok=True)

# List all files with '_lang.json' suffix
json_files = [os.path.join(input_directory, f) for f in os.listdir(input_directory) if f.endswith('_lang.json')]

# Process each JSON file
for file_path in json_files:
    process_json_file(file_path, output_directory)

print("All files processed or skipped if already existing.")


processing: ./dataset/outputs/hume\0_00-00-00.000_00-00-02.793_Phoebe_sadness_negative_lang.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-00.000_00-00-02.793_Phoebe_sadness_negative_lang_processed.json
processing: ./dataset/outputs/hume\0_00-00-00.000_00-00-05.672_Chandler_neutral_neutral_lang.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-00.000_00-00-05.672_Chandler_neutral_neutral_lang_processed.json
processing: ./dataset/outputs/hume\0_00-00-04.671_00-00-06.005_Monica_surprise_negative_lang.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-04.671_00-00-06.005_Monica_surprise_negative_lang_processed.json
processing: ./dataset/outputs/hume\0_00-00-05.881_00-00-07.383_The-Interviewer_neutral_neutral_lang.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-05.881_00-00-07.383_The-Interviewer_neutral_neutral_lang_processed.json
processing: ./dataset/outputs/hume\0_00-00-07.383_00-00-10.330_Chandler_neutral_neutral_

## 2. Merge face expressions to sentenses, and average scores for each emotions

In [15]:
import os
import json

def process_face_json_file(filepath, output_directory):
    # Determine output file path
    output_path = os.path.join(output_directory, os.path.basename(filepath).replace('_face.json', '_face_processed.json'))
    
    # Skip processing if the file already exists
    if os.path.exists(output_path):
        # print(f"Skipping existing file: {output_path}")
        return
    
    # Read JSON file
    with open(filepath, 'r') as file:
        data = json.load(file)
    
    # Navigate to the face predictions in JSON structure
    predictions = data[0]["results"]["predictions"]

    # Calculate average emotion scores
    emotion_scores = {}
    count_emotions = {}
    for pred in predictions:
        for model in pred["models"]["face"]["grouped_predictions"]:
            for emotion in model["predictions"][0]["emotions"]:
                if emotion["name"] in emotion_scores:
                    emotion_scores[emotion["name"]] += emotion["score"]
                    count_emotions[emotion["name"]] += 1
                else:
                    emotion_scores[emotion["name"]] = emotion["score"]
                    count_emotions[emotion["name"]] = 1
    
    # Averaging the scores
    average_emotion_scores = {emotion: score / count_emotions[emotion] for emotion, score in emotion_scores.items()}
    
    # Simplify the output format to just average emotion scores for face
    processed_data = {
        "face": average_emotion_scores
    }

    # Save processed data to a new file
    with open(output_path, 'w') as outfile:
        json.dump(processed_data, outfile, indent=4)
    print(f"Processed and saved: {output_path}")

# Directories
input_directory = "./dataset/outputs/hume"
output_directory = "./dataset/outputs/hume_processed"

# Create the output directory if it does not exist
os.makedirs(output_directory, exist_ok=True)

# List all files with '_face.json' suffix
json_files = [os.path.join(input_directory, f) for f in os.listdir(input_directory) if f.endswith('_face.json')]

# Process each JSON file
for file_path in json_files:
    process_face_json_file(file_path, output_directory)

print("All face files processed or skipped if already existing.")


Processed and saved: ./dataset/outputs/hume_processed\0_00-00-00.000_00-00-05.672_Chandler_neutral_neutral_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-05.881_00-00-07.383_The-Interviewer_neutral_neutral_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-07.383_00-00-10.330_Chandler_neutral_neutral_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-10.761_00-00-13.513_The-Interviewer_neutral_neutral_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-18.393_00-00-24.858_Chandler_surprise_positive_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-25.067_00-00-28.278_The-Interviewer_neutral_neutral_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-32.741_00-00-35.827_Chandler_neutral_neutral_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-32.741_00-00-38.455_The-In

Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-21.062_00-00-29.695_Ross_sadness_negative_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-33.575_00-00-36.618_Ross_sadness_negative_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-36.786_00-00-39.246_Phoebe_sadness_negative_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-39.414_00-00-42.583_Chandler_neutral_neutral_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-42.751_00-00-44.545_Rachel_anger_negative_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-44.545_00-00-46.798_Rachel_anger_negative_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-46.798_00-00-46.946_Rachel_sadness_negative_face_processed.json
Processed and saved: ./dataset/outputs/hume_processed\1007_00-00-47.005_00-00-51.550_Rachel_sadness_nega

## process prosody

In [16]:
import os
import json

def process_prosody_json_file(filepath, output_directory):
    full_emotions_list = [
        "Admiration", "Adoration", "Aesthetic Appreciation", "Amusement", "Anger", "Annoyance",
        "Anxiety", "Awe", "Awkwardness", "Boredom", "Calmness", "Concentration", "Confusion",
        "Contemplation", "Contempt", "Contentment", "Craving", "Desire", "Determination",
        "Disappointment", "Disapproval", "Disgust", "Distress", "Doubt", "Ecstasy", "Embarrassment",
        "Empathic Pain", "Enthusiasm", "Entrancement", "Envy", "Excitement", "Fear", "Gratitude",
        "Guilt", "Horror", "Interest", "Joy", "Love", "Nostalgia", "Pain", "Pride", "Realization",
        "Relief", "Romance", "Sadness", "Sarcasm", "Satisfaction", "Shame", "Surprise (negative)",
        "Surprise (positive)", "Sympathy", "Tiredness", "Triumph"
    ]

    output_path = os.path.join(output_directory, os.path.basename(filepath).replace('_prosody.json', '_prosody_processed.json'))
    
    if os.path.exists(output_path):
        # print(f"Skipping existing file: {output_path}")
        return
    
    with open(filepath, 'r') as file:
        data = json.load(file)

    if not data[0]["results"]["predictions"] or not data[0]["results"]["predictions"][0]["models"]["prosody"]["grouped_predictions"]:
        # Handle files with no predictions by setting all emotions to zero
        emotion_scores = {emotion: 0 for emotion in full_emotions_list}
    else:
        predictions = data[0]["results"]["predictions"][0]["models"]["prosody"]["grouped_predictions"][0]["predictions"]
        emotion_scores = {}
        count_emotions = {}

        for pred in predictions:
            for emotion in pred["emotions"]:
                if emotion["name"] in emotion_scores:
                    emotion_scores[emotion["name"]] += emotion["score"]
                    count_emotions[emotion["name"]] += 1
                else:
                    emotion_scores[emotion["name"]] = emotion["score"]
                    count_emotions[emotion["name"]] = 1

        emotion_scores = {emotion: score / count_emotions.get(emotion, 1) for emotion, score in emotion_scores.items()}

    processed_data = {
        "prosody": emotion_scores
    }

    with open(output_path, 'w') as outfile:
        json.dump(processed_data, outfile, indent=4)

    print(f"Processed and saved: {output_path}")

# Example usage:
input_directory = "./dataset/outputs/hume"
output_directory = "./dataset/outputs/hume_processed"
os.makedirs(output_directory, exist_ok=True)
json_files = [os.path.join(input_directory, f) for f in os.listdir(input_directory) if f.endswith('_prosody.json')]

for file_path in json_files:
    process_prosody_json_file(file_path, output_directory)

print("All prosody files processed or skipped if already existing.")


Processed and saved: ./dataset/outputs/hume_processed\0_00-00-00.000_00-00-05.672_Chandler_neutral_neutral_prosody_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-05.881_00-00-07.383_The-Interviewer_neutral_neutral_prosody_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-07.383_00-00-10.330_Chandler_neutral_neutral_prosody_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-10.761_00-00-13.513_The-Interviewer_neutral_neutral_prosody_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-18.393_00-00-24.858_Chandler_surprise_positive_prosody_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-25.067_00-00-28.278_The-Interviewer_neutral_neutral_prosody_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-32.741_00-00-35.827_Chandler_neutral_neutral_prosody_processed.json
Processed and saved: ./dataset/outputs/hume_processed\0_00-00-32.74

## Remove remove wrongly processed files from dev dataset

## Now we have simplified modalities in folder hume_processed
## Then we merge into one file with the information in the file names

In [17]:
import os
import json

def merge_json_files(input_directory, output_directory):
    # Create the output directory if it doesn't exist
    os.makedirs(output_directory, exist_ok=True)
    
    # Collect filenames without extension and modality suffix
    base_files = set(filename.rsplit("_", 2)[0] for filename in os.listdir(input_directory) if "_processed.json" in filename)

    for base_filename in base_files:
        # Check if all necessary files are present
        required_files = [
            f"{base_filename}_face_processed.json",
            f"{base_filename}_prosody_processed.json",
            f"{base_filename}_lang_processed.json"
        ]
        
        if all(os.path.exists(os.path.join(input_directory, fname)) for fname in required_files):
            # Check if the merged file already exists
            merged_filename = f"{base_filename}_merged.json"
            merged_path = os.path.join(output_directory, merged_filename)
            if os.path.exists(merged_path):
                print(f"Skipping {base_filename} - merged file already exists.")
                continue
            
            # Initialize the merged data dictionary
            merged_data = {"predicted": {"face": {}, "prosody": {}, "lang": {}}}
            
            # Merge the data from each modality file
            for modality in ["face", "prosody", "lang"]:
                modality_filename = f"{base_filename}_{modality}_processed.json"
                modality_path = os.path.join(input_directory, modality_filename)
                with open(modality_path, "r") as file:
                    modality_data = json.load(file)
                    merged_data["predicted"][modality] = modality_data.get(modality, {})
            
            # Save the merged data to a new JSON file in the output directory
            with open(merged_path, "w") as file:
                json.dump(merged_data, file, indent=4)
            
            print(f"Merged {base_filename} into {merged_filename}")
        else:
            print(f"Skipping {base_filename} - not all modalities are available.")

# Usage
input_directory = './dataset/outputs/hume_processed'
output_directory = './dataset/outputs/hume_processed_merged'
merge_json_files(input_directory, output_directory)


Skipping 26_00-00-09.718_00-00-15.974_Monica_neutral_neutral - not all modalities are available.
Merged 794_00-00-00.000_00-00-09.383_Ross_anger_negative into 794_00-00-00.000_00-00-09.383_Ross_anger_negative_merged.json
Skipping 26_00-00-00.000_00-00-03.711_Rachel_neutral_neutral - not all modalities are available.
Merged 359_00-00-00.000_00-00-01.333_Ross_surprise_positive into 359_00-00-00.000_00-00-01.333_Ross_surprise_positive_merged.json
Merged 897_00-00-22.814_00-00-25.399_Rachel_neutral_neutral into 897_00-00-22.814_00-00-25.399_Rachel_neutral_neutral_merged.json
Merged 1000_00-00-11.345_00-00-16.474_Joey_neutral_neutral into 1000_00-00-11.345_00-00-16.474_Joey_neutral_neutral_merged.json
Merged 548_00-00-18.810_00-00-25.107_Monica_neutral_neutral into 548_00-00-18.810_00-00-25.107_Monica_neutral_neutral_merged.json
Merged 964_00-00-27.903_00-00-29.864_Rachel_neutral_neutral into 964_00-00-27.903_00-00-29.864_Rachel_neutral_neutral_merged.json
Merged 910_00-00-30.697_00-00-33.3

# Add ground truth to json files, read from the file name

In [24]:
def process_predicted_files(predicted_directory, output_directory):
    # Create the output directory if it doesn't exist
    os.makedirs(output_directory, exist_ok=True)
    
    for filename in os.listdir(predicted_directory):
        if filename.endswith("_merged.json"):
            # Extract the metadata from the filename
            dialogue_id, offset_start, offset_end, speaker, emotion, sentiment, _ = filename[:-5].split("_")
            
            # Load the predicted emotions from the JSON file
            predicted_path = os.path.join(predicted_directory, filename)
            with open(predicted_path, "r") as file:
                predicted_data = json.load(file)
            
            # Construct the JSON structure with metadata
            merged_data = {
                "metadata": {
                    "dialogue_id": dialogue_id,
                    "time_start": offset_start,
                    "time_end": offset_end,
                    "speaker": speaker,
                    "emotion": emotion,
                    "sentiment": sentiment,
                    "file_name": filename.replace("_merged.json", "")
                },
                "predicted": predicted_data.get("predicted", {})
            }
            
            # Save the merged data to a new JSON file in the output directory
            output_filename = filename
            output_path = os.path.join(output_directory, output_filename)
            with open(output_path, "w") as file:
                json.dump(merged_data, file, indent=4)
            
            print(f"Processed {filename} into {output_filename}")

# Usage
output_directory = './dataset/outputs/merged_all'
predicted_directory = './dataset/outputs/hume_processed_merged'
process_predicted_files(predicted_directory, output_directory)

Processed 0_00-00-00.000_00-00-05.672_Chandler_neutral_neutral_merged.json into 0_00-00-00.000_00-00-05.672_Chandler_neutral_neutral_merged.json
Processed 0_00-00-05.881_00-00-07.383_The-Interviewer_neutral_neutral_merged.json into 0_00-00-05.881_00-00-07.383_The-Interviewer_neutral_neutral_merged.json
Processed 0_00-00-07.383_00-00-10.330_Chandler_neutral_neutral_merged.json into 0_00-00-07.383_00-00-10.330_Chandler_neutral_neutral_merged.json
Processed 0_00-00-10.761_00-00-13.513_The-Interviewer_neutral_neutral_merged.json into 0_00-00-10.761_00-00-13.513_The-Interviewer_neutral_neutral_merged.json
Processed 0_00-00-18.393_00-00-24.858_Chandler_surprise_positive_merged.json into 0_00-00-18.393_00-00-24.858_Chandler_surprise_positive_merged.json
Processed 0_00-00-25.067_00-00-28.278_The-Interviewer_neutral_neutral_merged.json into 0_00-00-25.067_00-00-28.278_The-Interviewer_neutral_neutral_merged.json
Processed 0_00-00-32.741_00-00-35.827_Chandler_neutral_neutral_merged.json into 0_00

In [ ]:
# Addon, read the csv files and add the text into the 

# The processed files will be saved into dataset/outputs/merged_all